In [7]:
import numpy as np
import pandas as pd
import os
import shutil
from flashgeotext.geotext import GeoText
import re
# import spacy
#
# nlp = spacy.load("en_core_web_lg")

In [8]:
record_col="UT (Unique WOS ID)"
outfile = r"C:\Users\radvanyi\PycharmProjects\ZSI_analytics\WOS\wos_extract\wos_records_concat.csv"

In [9]:
wos = pd.read_csv(outfile, sep="\t",low_memory=False)
print(f'Number of initial records: {len(wos)}')
metrix = pd.read_excel("sm_journal_classification.xlsx", sheet_name="Journal_Classification")


metrix = metrix.set_index([c for c in metrix.columns if "issn" not in c]).stack().reset_index()
metrix = metrix.rename(columns={'level_6':"issn_type", 0:"issn"})
metrix["issn"]=metrix["issn"].str.replace("-","").str.lower().str.strip()

wos["issn"] = wos["ISSN"].str.replace("-","").str.lower().str.strip()
wos["eissn"] = wos["eISSN"].str.replace("-","").str.lower().str.strip()
wos = wos.set_index([c for c in wos.columns if "issn" not in c]).stack().reset_index()
wos = wos.rename(columns={'level_71':"issn_var", 0:"issn"})

wos_merge = wos.merge(metrix, on="issn", how="left")
wos = wos_merge.sort_values(by="issn_var",ascending=False).drop_duplicates(subset=record_col)

# drop entries not indexed by metrix
wos = wos[~wos["Domain_English"].isna()]
# drop duplicates (based on doi)
wos = wos[~((~wos["DOI"].isna())&(wos["DOI"].duplicated(False)))]
wos = wos.drop_duplicates(subset=["Publication Type","Document Type","Authors","Article Title","Source Title","Publication Year"])
print(f'Number of filtered records: {len(wos)}')

Number of initial records: 27672
Number of filtered records: 24653


In [10]:
wos[["Article Title","Keywords Plus","Author Keywords"]].sample(100)

Article Title   
23070  Stochastic bias of colour-selected BAO tracers...  \
30139  A novel integrative approach elucidates fine-s...   
4538   Optimal Number of Clusters by Measuring Simila...   
34242  Analyzing the Noise Robustness of Deep Neural ...   
26727  Learning to Prompt for Open-Vocabulary Object ...   
...                                                  ...   
3290   Research on Reverse Skyline Query Algorithm Ba...   
45159  Using Recurrent Neural Network for Intelligent...   
21653  Output-Bounded and RBFNN-Based Position Tracki...   
43983  A Novel 3D Intelligent Cluster Method for Mali...   
11880  BlockHammer: Improving Flash Reliability by Ex...   

                                           Keywords Plus   
23070  DIGITAL SKY SURVEY; BARYON ACOUSTIC-OSCILLATIO...  \
30139  CHAOTIC GENETIC PATCHINESS; PELAGIC LARVAL DUR...   
4538                     VALIDATION; ALGORITHM; TUTORIAL   
34242                                   VISUAL ANALYTICS   
26727                                                NaN   
...                                                  ...   
3290                                           MAPREDUCE   
45159                                                NaN   
21653                           IMPEDANCE CONTROL; ROBOT   
43983  NETWORK INTRUSION DETECTION; DDOS DETECTION; A...   
11880  MEMORY; PERFORMANCE; RETENTION; ENDURANCE; OPT...   

                                         Author Keywords  
23070  galaxies: evolution; galaxies: haloes; galaxie...  
30139                                                NaN  
4538   Event-related potentials; Optimal number of cl...  
34242  Neurons; Visualization; Data visualization; Fe...  
26727                                                NaN  
...                                                  ...  
3290   Big Data; Database Management; Database Query;...  
45159  water resources; intelligent prediction; water...  
21653  Security tele-surgery; RBFNN; bilateral positi...  
43983  Auto encoder; DDos detection; Attack classific...  
11880  Reliability; Three-dimensional displays; Error...  

[100 rows x 3 columns]

In [11]:
kw_df = pd.DataFrame()
for c in ["Keywords Plus","Author Keywords"]:
    kwp = wos.groupby(record_col)[c].apply(lambda x: x.str.split(';')).explode().str.strip().str.upper()
    kwp.name = 'keyword_all'
    kw_df = pd.concat([kwp.reset_index(),kw_df],ignore_index=True)
kw_df = kw_df[~kw_df["keyword_all"].isna()].copy().drop(columns="level_1").drop_duplicates()
kw_df["keyword_all"] = kw_df["keyword_all"].apply(lambda x: re.sub("[\(\[].*?[\)\]]", "", x))
kw_df.head(100)

UT (Unique WOS ID)          keyword_all
0    WOS:000208863600266                 ANME
1    WOS:000208863600266       PYROSEQUENCING
2    WOS:000208863600266                  AOM
3    WOS:000208863600266  COMMUNITY STRUCTURE
4    WOS:000208863600266               NYEGGA
..                   ...                  ...
99   WOS:000286328200009      NORTH-EAST ASIA
100  WOS:000286328200009          PLEISTOCENE
101  WOS:000286328200009      SAKHALIN ISLAND
102  WOS:000286373200134      NEURAL NETWORKS
103  WOS:000286373200134          FUZZY LOGIC

[100 rows x 2 columns]

In [12]:
wos_kwd_concat = kw_df.groupby(record_col, as_index=False).agg({'keyword_all': '; '.join})
wos_kwd_concat.head()

UT (Unique WOS ID)                                        keyword_all
0  WOS:000208863600266  ANME; PYROSEQUENCING; AOM; COMMUNITY STRUCTURE...
1  WOS:000209236900010  ACTIVE PERCEPTION; SPARSE CODING; REINFORCEMEN...
2  WOS:000209331600009  SLEEP PATTERN; ELDER-CARE; PRESSURE SENSOR; NA...
3  WOS:000209571700012  PERSONALIZED MEDICINE; COMPLEX NETWORK; CLINIC...
4  WOS:000209810700046  CORROSION CHARACTERIZATION; FEATURE EXTRACTION...

In [13]:
# from keybert import KeyBERT
#
# kw_model = KeyBERT(model='all-mpnet-base-v2')
#
# def kwd_extract(text):
#     keywords = kw_model.extract_keywords(text,
#
#                                      keyphrase_ngram_range=(1, 2),
#
#                                      stop_words='english',
#
#                                      highlight=False,
#
#                                      top_n=3)
#     return "; ".join([i[0].upper() for i in keywords])
#
# kwd_extract(text="Artificial Intelligence: New Frontiers in Real-Time Inverse Scattering and Electromagnetic Imaging - In recent years, artificial intelligence (AI) techniques have been developed rapidly. With the ...")

In [14]:
wos.columns

Index(['Publication Type', 'Authors', 'Book Authors', 'Book Editors',
       'Book Group Authors', 'Author Full Names', 'Book Author Full Names',
       'Group Authors', 'Article Title', 'Source Title', 'Book Series Title',
       'Book Series Subtitle', 'Language', 'Document Type', 'Conference Title',
       'Conference Date', 'Conference Location', 'Conference Sponsor',
       'Conference Host', 'Author Keywords', 'Keywords Plus', 'Abstract',
       'Addresses', 'Affiliations', 'Reprint Addresses', 'Email Addresses',
       'Researcher Ids', 'ORCIDs', 'Funding Orgs', 'Funding Name Preferred',
       'Funding Text', 'Cited References', 'Cited Reference Count',
       'Times Cited, WoS Core', 'Times Cited, All Databases',
       '180 Day Usage Count', 'Since 2013 Usage Count', 'Publisher',
       'Publisher City', 'Publisher Address', 'ISSN', 'eISSN', 'ISBN',
       'Journal Abbreviation', 'Journal ISO Abbreviation', 'Publication Date',
       'Publication Year', 'Volume', 'Issue', 'Pa

In [25]:
geotext = GeoText()

def extract_location(input_text, key='countries'):
    anomalies = {"Malta":"Malta",
                 "Mongolia":"Mongolia",
                 "Quatar":"Qatar",
                 "Qatar":"Qatar",
                 "Ethiop":"Ethiopia",
                 "Nigeria":"Nigeria",
                 "BELAR":"Belarus",
                 "Venezuela":"Venezuela",
                 "Cyprus":"Cyprus",
                 "Ecuador":"Ecuador",
                 "U Arab":"United Arab Emirates",
                 "Syria":"Syria",
                 "Uganda":"Uganda",
                 "Yemen":"Yemen",
                 "Mali":"Mali",
                 "Senegal":"Senegal",
                 "Vatican":"Vatican",
                 "Uruguay":"Uruguay",
                 "Panama":"Panama",
                 "Fiji":"Fiji",
                 "Faroe":"Faroe Islands",
                 "Macedonia":"Macedonia",
                 'Mozambique':'Mozambique',
                 "Kuwait":"Kuwait",
                 "Libya":"Libya",
                 "Turkiy":"Turkey",
                 "Liberia":"Liberia",
                 "Namibia":"Namibia",
                 "Ivoire":"Ivory Coast",
                 "Guatemala":"Gutemala",
                 "Paraguay":"Paraguay",
                 "Honduras":"Honduras",
                 "Nicaragua":"Nicaragua",
                 "Trinidad":"Trinidad & Tobago",
                 "Liechtenstein":"Liechtenstein",
                 "Greenland":"Denmark"}

    extracted = geotext.extract(input_text=input_text)
    found = extracted[key].keys()
    if len(sorted(found))>0:
        return sorted(found)[0]
    elif key=='countries':
        for i  in ['Scotland','Wales','England', 'N Ireland']:
            if i in input_text:
                return 'United Kingdom'
        for j in anomalies.keys():
            if j in input_text:
                return anomalies.get(j)
    else:
        return None

with open('../eu_members.txt',"r") as f:
    eu_countries=f.readline().split(",")
    eu_countries=[i.strip() for i in eu_countries]

def country_type(country):
    if country in eu_countries:
        return "EU"
    elif country=="China":
        return "China"
    elif country in ["Switzerland", 'Norway','United Kingdom']:
        return "Non-EU associate"
    else:
        return "Other"


In [26]:
locations = wos.groupby(record_col)["Addresses"].apply(lambda x: x.str.split('[')).explode().reset_index().drop(columns="level_1")
locations = locations[locations["Addresses"]!=""].copy()
locations["Address"] = locations["Addresses"].apply(lambda x:x.split("]")[-1])
locations["Authors_of_address"] = locations["Addresses"].apply(lambda x:x.split("]")[0])
locations["Country"]=locations['Address'].apply(lambda x: extract_location(input_text=x, key='countries'))
locations["City"]=locations['Address'].apply(lambda x: extract_location(input_text=x, key='cities'))
locations["Country_Type"] = locations["Country"].apply(lambda x: country_type(x))

In [32]:
scope_types = ["EU","China","Non-EU associate"]
locations=locations[locations["Country_Type"].isin(scope_types)]

In [65]:
univ_locations = locations[[record_col,"Address","Country","City","Country_Type"]].copy()
univ_locations["Institution"] = univ_locations["Address"].apply(lambda x: x.split(",")[0])
univ_locations = univ_locations.drop_duplicates()
univ_locations.head()

UT (Unique WOS ID)                                            Address   
1  WOS:000208863600266   Univ Bergen, Ctr Geobiol, Dept Biol, N-5020 B...  \
2  WOS:000208863600266   Chinese Acad Sci, Guangzhou Inst Geochem, Gua...   
3  WOS:000208863600266   Univ Bergen, Dept Earth Sci, N-5020 Bergen, N...   
5  WOS:000209236900010   Goethe Univ Frankfurt, Frankfurt Inst Adv Stu...   
6  WOS:000209236900010   Ecole Normale Super Cachan Bretagne, Bruz, Fr...   

   Country              City      Country_Type   
1   Norway            Bergen  Non-EU associate  \
2    China         Guangzhou             China   
3   Norway            Bergen  Non-EU associate   
5  Germany  Frankfurt (Oder)                EU   
6   France            Cachan                EU   

                            Institution  
1                           Univ Bergen  
2                      Chinese Acad Sci  
3                           Univ Bergen  
5                 Goethe Univ Frankfurt  
6   Ecole Normale Super Cachan Bretagne

In [38]:
import hashlib

def md5hash(s: str):
    return hashlib.md5(s.encode('utf-8')).hexdigest()

In [39]:
author_locations = locations.groupby([record_col,"Country","Country_Type"])["Authors_of_address"].apply(lambda x: x.str.split(';')).explode().reset_index().drop(columns="level_3")
author_locations["Author_name"] = author_locations["Authors_of_address"].str.strip()
author_locations = author_locations.drop(columns="Authors_of_address")
author_locations["author_str_id"] = author_locations["Author_name"].apply(lambda x:''.join(filter(str.isalnum, x.lower())))
author_locations["author_str_id"] = author_locations["author_str_id"].apply(md5hash)
author_locations = author_locations.drop(columns="Author_name")
author_locations.head()

UT (Unique WOS ID) Country      Country_Type   
0  WOS:000208863600266   China             China  \
1  WOS:000208863600266  Norway  Non-EU associate   
2  WOS:000208863600266  Norway  Non-EU associate   
3  WOS:000208863600266  Norway  Non-EU associate   
4  WOS:000208863600266  Norway  Non-EU associate   

                      author_str_id  
0  5dfb4f0408a2cc8b7f36f5516938b62c  
1  d603b89121a1f279bf03b6f65d1389fa  
2  2fcb84e544f1558ead61dcf846027b7d  
3  6550a1d5fbd1b643f4732d40f2ed4d78  
4  56485e2bd170d199887af88f3d0a9777

In [44]:
author_locations[author_locations['author_str_id'].duplicated(False)]

UT (Unique WOS ID)         Country      Country_Type   
0       WOS:000208863600266           China             China  \
6       WOS:000209236900010           China             China   
7       WOS:000209236900010           China             China   
8       WOS:000209236900010          France                EU   
10      WOS:000209236900010         Germany                EU   
...                     ...             ...               ...   
321236  WOS:000953367000001           China             China   
321237  WOS:000953367000001           China             China   
321238  WOS:000953367000001           China             China   
321239  WOS:000953367000001           China             China   
321241  WOS:000953367000001  United Kingdom  Non-EU associate   

                           author_str_id  
0       5dfb4f0408a2cc8b7f36f5516938b62c  
6       b406b8485c286091a46aca4999f294d3  
7       abf37b879540b7c2eeb86787a467de29  
8       2c559a54c654ab6dbc23d20ae82a0501  
10      2c559a54c654ab6dbc23d20ae82a0501  
...                                  ...  
321236  99ef5c82ba66e07f9aa2d3f9fc7c45f7  
321237  d013bf53d094540f90db9224b3eb9922  
321238  702962f6fe47bac08520ae556a8e0e02  
321239  99ef5c82ba66e07f9aa2d3f9fc7c45f7  
321241  9cc42be570a5464bca0ea4b6b39d0271  

[277884 rows x 4 columns]

In [51]:
author_primary_region = author_locations.sort_values(by="Country_Type").drop_duplicates(subset=[record_col,"author_str_id"])
# author_primary_region

china=author_primary_region[author_primary_region["Country_Type"]=="China"][record_col].unique()
eu=author_primary_region[author_primary_region["Country_Type"]=="EU"][record_col].unique()
assoc=author_primary_region[author_primary_region["Country_Type"]=="Non-EU associate"][record_col].unique()


# records that have distinct authors with different country affiliations
valid_scope = wos[((wos[record_col].isin(china))
         &
         ((wos[record_col].isin(eu))
         |
         (wos[record_col].isin(assoc))))][record_col].unique()

In [54]:
author_primary_region.head()

UT (Unique WOS ID) Country Country_Type   
0       WOS:000208863600266   China        China  \
299168  WOS:000840488600001   China        China   
299169  WOS:000840488600001   China        China   
101376  WOS:000434663200012   China        China   
101374  WOS:000434663200012   China        China   

                           author_str_id  
0       5dfb4f0408a2cc8b7f36f5516938b62c  
299168  3462304c908993a828cdd0ff91ea4aaa  
299169  68ab59c442eb882af13a8273439cf840  
101376  304c36b8b677f41a489894dc66a8461c  
101374  c04795fe195dcadb58bed5c81125ea35

In [52]:
print(f'Number of records: {len(wos)}')
print(f'Number of valid cooperation records: {len(valid_scope)}')

Number of records: 24653
Number of valid records: 22081


In [66]:
wos = wos[wos[record_col].isin(valid_scope)]
locations = locations[locations[record_col].isin(valid_scope)]
univ_locations = univ_locations[univ_locations[record_col].isin(valid_scope)]
author_locations = author_locations[author_locations[record_col].isin(valid_scope)]
author_primary_region = author_locations[author_locations[record_col].isin(valid_scope)]

In [56]:
affiliations = wos.groupby(record_col)["Affiliations"].apply(lambda x: x.str.split(';')).explode().reset_index().drop(columns="level_1")
affiliations["Affiliations"] = affiliations["Affiliations"].str.strip().str.upper().fillna("UNKNOWN")
affiliations = affiliations.drop_duplicates()

In [67]:
affiliations["Affiliations"].value_counts()

Affiliations
CHINESE ACADEMY OF SCIENCES                            2688
UNIVERSITY OF LONDON                                   1251
UDICE-FRENCH RESEARCH UNIVERSITIES                     1038
CENTRE NATIONAL DE LA RECHERCHE SCIENTIFIQUE (CNRS)     978
TSINGHUA UNIVERSITY                                     960
                                                       ... 
ITALIAN INSTITUTE FOR GENOMIC MEDICINE (IIGM)             1
SHENYANG INSTITUTE OF ENGINEERING                         1
XIANYANG NORMAL UNIVERSITY                                1
AGILENT TECHNOLOGIES                                      1
UNIVERSIDAD DE ESPECIALIDADES ESPIRITU SANTO              1
Name: count, Length: 6117, dtype: int64

In [68]:
univ_locations["Institution"].value_counts()

Institution
 Chinese Acad Sci                                     2708
 Tsinghua Univ                                        1170
 Shanghai Jiao Tong Univ                               978
 Zhejiang Univ                                         902
 Univ Chinese Acad Sci                                 753
                                                      ... 
 Univ Namur                                              1
 Qianhai Inst Innovat Res                                1
 UN                                                      1
 Vienna Int Ctr                                          1
 Engn Res Ctr Urban Underground Space Dev Zhejiang       1
Name: count, Length: 11670, dtype: int64

In [61]:
univ_locations[record_col].nunique()

22081

In [62]:
affiliations[record_col].nunique()

22081

In [63]:
univ_locations["Institution"].value_counts().sum()

99343

In [64]:
affiliations["Affiliations"].value_counts().sum()

130533

In [70]:
aff_ = wos.groupby(record_col)["Affiliations"].apply(lambda x: x.str.split(';')).explode().reset_index().drop(columns="level_1")
loc_ = wos.groupby(record_col)["Addresses"].apply(lambda x: x.str.split('[')).explode().reset_index().drop(columns="level_1")
print(len(aff_),len(loc_))

158916 162684


In [ ]:
unique_inst = sorted([i.split(" ") for i in list(affiliations["Affiliations"].unique())], key=len)
# unique_inst = [[''.join(filter(str.isalnum, i)) for i in i_list] for i_list in unique_inst]
unique_inst = [[i.strip(",").strip("(").strip(")") for i in i_list] for i_list in unique_inst]
unique_inst

In [ ]:
def institution_chunk_norris(text):
    for i in unique_inst:
        text_split=text.split(" ")
        text_split=[i.strip(",").strip("(").strip(")") for i in text_split]
        overlap = all(token in text_split for token in i)
        if overlap:
            return (" ".join(i))
    return "ERROR"

In [ ]:
affiliations["Affiliations_merged"] = affiliations["Affiliations"].apply(lambda x: institution_chunk_norris(x))

In [ ]:
affiliations["Affiliations"].value_counts()

In [ ]:
affiliations["Affiliations_merged"].value_counts()

In [ ]:
affiliations[affiliations["Affiliations_merged"]=="ERROR"]

In [ ]:
from nltk.metrics import edit_distance
from nltk.metrics import edit_distance_align
#results = df.apply(lambda x: edit_distance(x["column1"], x["column2"]), axis=1)

In [ ]:
affiliations = affiliations.merge(univ_locations, on=record_col)

In [ ]:
affiliations["Affiliations"] = affiliations["Affiliations"].str.upper().str.strip()
affiliations["Institution"] = affiliations["Institution"].str.upper().str.strip()

affiliations["levehnstein"] = affiliations.apply(
    lambda x: edit_distance(x["Affiliations"], x["Institution"]), axis=1)
affiliations.head()

In [ ]:
def tok_overlap(lon_str, short_str):
    l,s = lon_str.split(" "), short_str.split(" ")
    # create a pairwise distance matrix using NumPy
    distance_matrix = np.fromfunction(np.vectorize(lambda i, j: edit_distance(l[int(i)], s[int(j)])), shape=(len(l), len(s)))
    distance_frame = pd.DataFrame(data=distance_matrix, columns=s, index=l)

    return min(distance_frame.min().sum(),distance_frame.T.min().sum())

# lon=("UNIVERSITY","AMSTERDAM","TECHNICAL", "LOCAL")
# sho=("UNIV","AMSTER","TECH","LOCAL")
# tok_overlap(lon_str=" ".join(lon),short_str=" ".join(sho)).min().sum()

In [ ]:
tok_overlap(lon_str=" ".join(l),short_str=" ".join(s)).shape

In [ ]:
affiliations["token_overlap"] = affiliations.apply(
    lambda x: tok_overlap(x["Affiliations"], x["Institution"]), axis=1)
affiliations.head()

In [ ]:
affiliations.sort_values(by=[record_col,"Affiliations","token_overlap"], ascending=[False,False,True]).drop_duplicates(subset=[record_col,"Affiliations"])

In [ ]:
helper = affiliations.sort_values(by=["Affiliations","token_overlap"], ascending=[False,True]).drop_duplicates(subset=[record_col,"Affiliations"])
afh = helper[["Affiliations","Institution","Country"]]
afh.groupby("Affiliations")["Institution"].agg(pd.Series.mode)

In [ ]:
afh.groupby("Affiliations")["Country"].agg(pd.Series.mode)

In [ ]:
helper1 = affiliations.sort_values(by=["Affiliations","token_overlap"], ascending=[False,True]).drop_duplicates(subset=[record_col,"Affiliations"])
afh1 = helper1[["Affiliations","Institution","City","Country","Country_Type"]]
mode1_i = afh1.groupby("Affiliations")["Institution"].apply(pd.Series.mode).reset_index()
mode1_c = afh1.groupby("Affiliations")["Country"].apply(pd.Series.mode).reset_index()
mode1_city = afh1.groupby("Affiliations")["City"].apply(pd.Series.mode).reset_index()
mode1_type = afh1.groupby("Affiliations")["Country_Type"].apply(pd.Series.mode).reset_index()

helper2 = affiliations.sort_values(by=["Affiliations","levehnstein"], ascending=[False,True]).drop_duplicates(subset=[record_col,"Affiliations"])
afh2 = helper2[["Affiliations","Institution","City","Country","Country_Type"]]
mode2_i = afh2.groupby("Affiliations")["Institution"].apply(pd.Series.mode).reset_index()
mode2_c = afh2.groupby("Affiliations")["Country"].apply(pd.Series.mode).reset_index()
mode2_city = afh2.groupby("Affiliations")["City"].apply(pd.Series.mode).reset_index()
mode2_type = afh2.groupby("Affiliations")["Country_Type"].apply(pd.Series.mode).reset_index()

mode_i = pd.concat([mode1_i,mode2_i],ignore_index=True)[["Affiliations","Institution"]].groupby("Affiliations")["Institution"].agg(
    lambda x: pd.Series.mode(x)[0])
mode_c = pd.concat([mode1_c,mode2_c],ignore_index=True)[["Affiliations","Country"]].groupby("Affiliations")["Country"].agg(
    lambda x: pd.Series.mode(x)[0])
mode_city = pd.concat([mode1_city,mode2_city],ignore_index=True)[["Affiliations","City"]].groupby("Affiliations")["City"].agg(
    lambda x: pd.Series.mode(x)[0])
mode_type = pd.concat([mode1_type,mode2_type],ignore_index=True)[["Affiliations","Country_Type"]].groupby("Affiliations")["Country_Type"].agg(
    lambda x: pd.Series.mode(x)[0])

In [ ]:
from functools import reduce
dfs = [mode_i, mode_c, mode_city, mode_type]
mode_final = reduce(lambda left,right: pd.merge(left,right,on='Affiliations'), dfs)
mode_final = mode_final.reset_index()
mode_final.columns = ["Affiliations","Institution (short name from address)","Country_candidate","City_candidate","Country_type_candidate"]
mode_final

In [ ]:
aff_lookup = affiliations[["Affiliations","Institution","levehnstein"]].drop_duplicates().sort_values(by=["Affiliations","levehnstein"],ascending=[True,True])
aff_lookup

In [ ]:
aff_lookup_levehnstein = aff_lookup.copy()
aff_lookup_overlap = aff_lookup.copy()
inst_short = sorted([i.split(" ") for i in list(aff_lookup_overlap["Institution"].unique())], key=len)
inst_short

In [ ]:
aff_lookup.drop_duplicates(subset="Affiliations")

In [ ]:
# aff_m = pd.DataFrame(affiliations["Affiliations"].unique(), columns=["Affiliations"])
# inst_m = pd.DataFrame(affiliations[["Institution","Country_Type","Country","City"]].drop_duplicates(),columns=["Institution","Country_Type","Country","City"])
#
# aff_lookup = aff_m.merge(inst_m, how='cross')
#
# # aff_lookup["levehnstein"] = aff_lookup.apply(
# #     lambda x: edit_distance(x["Affiliations"], x["Institution"]), axis=1)
#
# aff_lookup.assign(distance=[*map(edit_distance, aff_lookup.Affiliations, aff_lookup.Institution)])

In [ ]:
affiliations["levehnstein"].plot(kind="hist")

In [ ]:
affiliations["token_overlap"].plot(kind="hist")

In [ ]:
affiliations[affiliations["Affiliations"].str.contains("A*STAR",regex=False)]

In [ ]:
affiliations = affiliations.sort_values(by=[record_col,"Affiliations","levehnstein"], ascending=[False,False,True])
affiliations_merge = affiliations.drop_duplicates(subset=[record_col,"Affiliations"])
affiliations_merge.head(10)

In [ ]:
wos_cat = wos.groupby(record_col)["WoS Categories"].apply(lambda x: x.str.split(';')).explode().reset_index().drop(columns="level_1")
wos_cat["WoS Categories"].value_counts()

In [ ]:
wos_areas = wos.groupby(record_col)["Research Areas"].apply(lambda x: x.str.split(';')).explode().reset_index().drop(columns="level_1")
wos_areas["Research Areas"] = wos_areas["Research Areas"].str.strip()
wos_areas["Research Areas"].value_counts()

In [ ]:
wos_areas["Research Areas"].value_counts()

In [ ]:
[c for c in wos.columns if "_English" in c]

In [ ]:
import seaborn as sns
from matplotlib.ticker import MaxNLocator
import math

In [ ]:
wos = wos[((wos["Publication Year"]<2023) & (~wos['Domain_English'].isna()))]

metrix_levels = [c for c in wos.columns if "_English" in c]
for m in metrix_levels:
    wos[m] = wos[m].replace({"article-level classification":"Miscellaneous"})


In [ ]:
wos

In [ ]:
metrix_levels

In [ ]:
outdir="wos_processed_data"

In [ ]:
os.makedirs(outdir, exist_ok=True)

wos.to_excel(f"{outdir}/wos_processed.xlsx", index=False)

locations.drop(columns="Addresses").to_excel(f"{outdir}/wos_addresses.xlsx", index=False)

affiliations_merge.to_excel(f"{outdir}/wos_affiliations.xlsx", index=False)

author_locations.to_excel(f"{outdir}/wos_author_locations.xlsx", index=False)

univ_locations.to_excel(f"{outdir}/wos_univ_locations.xlsx", index=False)
mode_final.to_excel(f"{outdir}/wos_univ_locations_v2.xlsx", index=False)

In [ ]:
kw_df.to_excel(f"{outdir}/keywords.xlsx", index=False)
wos_nlp.to_excel(f"{outdir}/wos_nlp.xlsx", index=False)

In [ ]:
# wos_nlp = wos[[record_col,"Article Title","Abstract"]]
wos = wos.merge(wos_kwd_concat, on=record_col)
wos["Document"] = wos["Article Title"].str.cat(wos[["Abstract", "keyword_all"]].fillna(""), sep=' - ')
# wos_kwd_test["BERT_KWDS"] = wos_kwd_test["Document"].map(kwd_extract)

vectors = list()
vector_norms = list()

for doc in nlp.pipe(wos['Document'].astype('unicode').values, batch_size=100,
                    n_process=4):
    vectors.append(doc.vector)
    vector_norms.append(doc.vector_norm)

wos['vector'] = vectors
wos['vector_norm'] = vector_norms
wos['vector_norm'].plot(kind="hist")
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt
% matplotlib inline

vector_data = pd.DataFrame(wos["vector"].to_list(), index=wos[record_col]).reset_index()
vector_data.head()

labels = vector_data.values[:, 0]
record_vectors = vector_data.values[:, 1:]

tsne_model = TSNE(perplexity=30, n_components=2, init='pca', n_iter=5000, random_state=42, metric='cosine')
tnse_2d = tsne_model.fit_transform(record_vectors)
tnse_data = pd.DataFrame(tnse_2d, index=labels).reset_index()
tnse_data.columns = [record_col, "TNSE-X", "TNSE-Y"]
tnse_data.head()
import seaborn as sns

wos_plot = wos.merge(tnse_data, on=record_col)

g = sns.scatterplot(wos_plot[wos_plot["Domain_English"] != 'article-level classification'], x="TNSE-X", y="TNSE-Y",
                    hue='Domain_English', s=1)
g.legend(bbox_to_anchor=(1.05, 1), loc=2, borderaxespad=0.)
wos_plot.head()
wos_nlp = wos_plot[[record_col, "Document", "keyword_all", "TNSE-X", "TNSE-Y"]]
g = sns.kdeplot(
    data=wos_plot[wos_plot["Domain_English"] != 'article-level classification'],
    x="TNSE-X", y="TNSE-Y", hue='Domain_English',
    thresh=.1,
)
wos.columns

# Domain

In [ ]:
group = 'Domain_English'
data = wos.groupby(group, as_index=False)[record_col].nunique().sort_values(ascending=False, by=record_col)
data

In [ ]:
sns.barplot(data, x=record_col, y=group)

In [ ]:
# group = ['Publication Year','Domain_English']
# data = wos.groupby(group, as_index=False)[record_col].nunique().sort_values(ascending=False, by=group+[record_col])
# data

In [ ]:
# group = ['Publication Year','Domain_English']
# data = wos.groupby(group)[record_col].nunique().unstack(fill_value=0).stack().reset_index().rename(columns={0:record_col}).sort_values(ascending=False, by=group+[record_col])
# data

In [ ]:
# g=sns.lineplot(data.sort_values(ascending=True, by=group[-1]),y=record_col,x=group[0], hue=group[-1])
# g.set(xticks=list(range(2012,2022+1,2)))
# g.legend(title=None)

# Field

In [ ]:
# group = ['Publication Year',"Domain_English",'Field_English']
# data = wos.groupby(group, as_index=False)[record_col].nunique().sort_values(ascending=False, by=group+[record_col])
# data

In [ ]:
# g = sns.FacetGrid(data, col="Domain_English", col_wrap=3, height=5)
# g.map_dataframe(sns.lineplot,x=group[0],y=record_col,hue=group[-1])
# g.set_titles(col_template="{col_name}")
# g.set(xticks=list(range(2012,2022+1,2)))
# # g.add_legend()

In [ ]:
# import matplotlib.pyplot as plt
# for cat in sorted(data[group[-2]].unique()):
#     sub_data = data[data[group[-2]]==cat]
#     sub_data = sub_data.complete({group[0]:range(int(data[group[0]].min()), int(data[group[0]].max()) + 1)}
#                                  ,group[-1],fill_value=0)
#     g=sns.lineplot(sub_data.sort_values(ascending=True, by=group[-1]),y=record_col,x=group[0], hue=group[-1])
#     g.set(xticks=list(range(2012,2022+1,2)))
#     g.legend(title=None)
#     g.set_title(cat)
#     g.yaxis.set_major_locator(MaxNLocator(integer=True))
#     plt.show()

# SubField

In [ ]:
# group = ['Publication Year',"Domain_English",'Field_English',"SubField_English"]
# data = wos.groupby(group, as_index=False)[record_col].nunique().sort_values(ascending=False, by=group+[record_col])
# data

In [ ]:
# import matplotlib.pyplot as plt
# for cat in sorted(data[group[-2]].unique()):
#     sub_data = data[data[group[-2]]==cat]
#     sub_data = sub_data.complete({group[0]:range(int(data[group[0]].min()), int(data[group[0]].max()) + 1)}
#                                  ,group[-1],fill_value=0)
#     g=sns.lineplot(sub_data.sort_values(ascending=True, by=group[-1]),y=record_col,x=group[0], hue=group[-1])
#     g.set(xticks=list(range(2012,2022+1,2)))
#     g.legend(title=None,bbox_to_anchor=(1.05, 1), loc=2, borderaxespad=0., ncols=math.ceil(len(g.legend_.texts)/12))
#     g.set_title(cat)
#     plt.show()